<a href="https://colab.research.google.com/github/sacculifer/NLPower-capstone-project/blob/Alex/NER_Alex.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install transformers
#!pip install spacy
!pip install geopy
!pip install pycountry

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.7 MB 5.3 MB/s 
     |████████████████████████████████| 6.6 MB 37.3 MB/s 
     |████████████████████████████████| 101 kB 10.8 MB/s 
     |████████████████████████████████| 596 kB 28.3 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [10]:
import pandas as pd
import pycountry
import random

from transformers import AutoTokenizer, AutoModelForTokenClassification
from transformers import pipeline
from google.colab import files
from geopy.geocoders import Nominatim

In [11]:
#df = pd.read_csv("train.csv")
ner_results = pd.read_csv("output-2.csv")

In [176]:
tweets = df['text']

In [177]:
tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")
model = AutoModelForTokenClassification.from_pretrained("dslim/bert-base-NER")

nlp = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy='average')
#nlp = pipeline("ner", aggregation_strategy='average')

In [179]:
ner_results = nlp(list(tweets))
ner_results = pd.DataFrame(ner_results)

In [180]:
ner_results['locations'] = ""
for i in range(len(ner_results[0])):
  ner_results['locations'][i] = []
  for j in range(11):
    if ner_results[j][i] is None:
      continue
    if ner_results[j][i]['entity_group'] == 'LOC' and ner_results[j][i]['score'] > 0.8:
      ner_results['locations'][i].append(ner_results[j][i]['word'])
    else:
      continue

In [182]:
ner_results['location_1'] = [next(iter(l), None) for l in ner_results['locations']]

In [ ]:
# Initialize Nominatim API
geolocator = Nominatim(user_agent="MyApp")

In [ ]:
ner_results['lat1'] = ""
ner_results['long1'] = ""
for i in range(len(ner_results)):
  if pd.isna(ner_results['location_1'][i]) == True:
    continue
  else:
    try:
      print(str(i) + ': ')
      location = geolocator.geocode(ner_results['location_1'][i])
      ner_results['lat1'][i] = location.latitude
      ner_results['long1'][i] = location.longitude
      print(str(ner_results['lat1'][i]))
    except:
      pass

In [ ]:
ner_results['country'] = ""
ner_results['state'] = ""
ner_results['city'] = ""

for i in range(len(ner_results)):
  if pd.isna(ner_results['location_1'][i]) == True:
    continue
  else:
    try:
      location = geolocator.reverse(str(ner_results['lat1'][i]) + " , " + str(ner_results['long1'][i]), language = 'en')
      address = location.raw['address']
      print(str(i) + ': ')
      ner_results['city'][i] = address.get('city', '')
      ner_results['state'][i] = address.get('state', '')
      ner_results['country'][i] = address.get('country', '')
      print(str(ner_results['city'][i]) + str(ner_results['state'][i]) + str(ner_results['country'][i]))
    except:
      pass

In [35]:
location = geolocator.reverse(str(ner_results['lat1'][1]) + " , " + str(ner_results['long1'][1]), language = 'en')
address = location.raw['address']
address

{'ISO3166-2-lvl4': 'CA-SK',
 'country': 'Canada',
 'country_code': 'ca',
 'house_number': '809',
 'postcode': 'S0J 1L0',
 'road': 'La Ronge Avenue',
 'state': 'Saskatchewan',
 'town': 'La Ronge'}

In [ ]:
ner_results

In [ ]:
ner_results.to_csv('output.csv')
files.download('output.csv')

In [ ]:
geolocator.geocode("['Japan', 'Germany']")

In [ ]:
ner_results

In [12]:
!pip install plotly
!pip install pyyaml==5.4.1

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 636 kB 4.9 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 6.0
    Uninstalling PyYAML-6.0:
      Successfully uninstalled PyYAML-6.0


In [1]:
import plotly.express as px



/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)


In [2]:
df = px.data.gapminder().query("year == 2007")

In [3]:
df

country continent  year  lifeExp       pop     gdpPercap  \
11           Afghanistan      Asia  2007   43.828  31889923    974.580338   
23               Albania    Europe  2007   76.423   3600523   5937.029526   
35               Algeria    Africa  2007   72.301  33333216   6223.367465   
47                Angola    Africa  2007   42.731  12420476   4797.231267   
59             Argentina  Americas  2007   75.320  40301927  12779.379640   
...                  ...       ...   ...      ...       ...           ...   
1655             Vietnam      Asia  2007   74.249  85262356   2441.576404   
1667  West Bank and Gaza      Asia  2007   73.422   4018332   3025.349798   
1679         Yemen, Rep.      Asia  2007   62.698  22211743   2280.769906   
1691              Zambia    Africa  2007   42.384  11746035   1271.211593   
1703            Zimbabwe    Africa  2007   43.487  12311143    469.709298   

     iso_alpha  iso_num  
11         AFG        4  
23         ALB        8  
35         DZA       12  
47         AGO       24  
59         ARG       32  
...        ...      ...  
1655       VNM      704  
1667       PSE      275  
1679       YEM      887  
1691       ZMB      894  
1703       ZWE      716  

[142 rows x 8 columns]

In [52]:
ner_results

Unnamed: 0  Unnamed: 0.1  \
0              0             0   
1              1             1   
2              2             2   
3              3             3   
4              4             4   
...          ...           ...   
7608        7608          7608   
7609        7609          7609   
7610        7610          7610   
7611        7611          7611   
7612        7612          7612   

                                                      0  \
0                                                   NaN   
1     {'entity_group': 'LOC', 'score': 0.99139684, '...   
2                                                   NaN   
3     {'entity_group': 'LOC', 'score': 0.99977106, '...   
4     {'entity_group': 'LOC', 'score': 0.3436687, 'w...   
...                                                 ...   
7608                                                NaN   
7609  {'entity_group': 'LOC', 'score': 0.999671, 'wo...   
7610  {'entity_group': 'ORG', 'score': 0.3611209, 'w...   
7611  {'entity_group': 'LOC', 'score': 0.99159527, '...   
7612  {'entity_group': 'MISC', 'score': 0.9483804, '...   

                                                      1    2    3    4    5  \
0                                                   NaN  NaN  NaN  NaN  NaN   
1     {'entity_group': 'LOC', 'score': 0.9997851, 'w...  NaN  NaN  NaN  NaN   
2                                                   NaN  NaN  NaN  NaN  NaN   
3                                                   NaN  NaN  NaN  NaN  NaN   
4     {'entity_group': 'LOC', 'score': 0.9913408, 'w...  NaN  NaN  NaN  NaN   
...                                                 ...  ...  ...  ...  ...   
7608                                                NaN  NaN  NaN  NaN  NaN   
7609  {'entity_group': 'MISC', 'score': 0.7334061, '...  NaN  NaN  NaN  NaN   
7610  {'entity_group': 'LOC', 'score': 0.86989534, '...  NaN  NaN  NaN  NaN   
7611                                                NaN  NaN  NaN  NaN  NaN   
7612  {'entity_group': 'ORG', 'score': 0.9987706, 'w...  NaN  NaN  NaN  NaN   

        6    7  ...                                               text  \
0     NaN  NaN  ...  Our Deeds are the Reason of this #earthquake M...   
1     NaN  NaN  ...             Forest fire near La Ronge Sask. Canada   
2     NaN  NaN  ...  All residents asked to 'shelter in place' are ...   
3     NaN  NaN  ...  13,000 people receive #wildfires evacuation or...   
4     NaN  NaN  ...  Just got sent this photo from Ruby #Alaska as ...   
...   ...  ...  ...                                                ...   
7608  NaN  NaN  ...  Two giant cranes holding a bridge collapse int...   
7609  NaN  NaN  ...  @aria_ahrary @TheTawniest The out of control w...   
7610  NaN  NaN  ...  M1.94 [01:04 UTC]?5km S of Volcano Hawaii. htt...   
7611  NaN  NaN  ...  Police investigating after an e-bike collided ...   
7612  NaN  NaN  ...  The Latest: More Homes Razed by Northern Calif...   

                        locations       location_1       lat1       long1  \
0                              []              NaN        NaN         NaN   
1     ['La Ronge Sask', 'Canada']    La Ronge Sask  55.100528 -105.290048   
2                              []              NaN        NaN         NaN   
3                  ['California']       California  36.701463 -118.755997   
4                      ['Alaska']           Alaska  64.445961 -149.680909   
...                           ...              ...        ...         ...   
7608                           []              NaN        NaN         NaN   
7609               ['California']       California  36.701463 -118.755997   
7610                   ['Hawaii']           Hawaii  19.593802 -155.428370   
7611          ['Little Portugal']  Little Portugal  43.647413  -79.431116   
7612                           []              NaN        NaN         NaN   

            country         state     city  year cat  
0               NaN           NaN      NaN  2014   3  
1            Ca

In [267]:
input_countries = df2['country']

countries1 = {}
for country in pycountry.countries:
    countries1[country.name] = country.alpha_3

codes = [countries1.get(country, 'Unknown code') for country in input_countries]

df2['codes'] = codes

In [50]:
ner_results['year'] = [random.randrange(2011, 2018, 1) for i in range(len(ner_results))]

In [51]:
ner_results['cat'] = [random.randrange(1, 11, 1) for i in range(len(ner_results))]

In [44]:
df = ner_results['country'].value_counts()

In [161]:
set(df2['cat'])


{1, 2, 3, 4, 5, 6, 7, 8, 9, 10}

In [182]:
df2 = ner_results[['country', 'year', 'cat']]
df2 = df2.groupby(['country', 'year', 'cat'])['country'].count()
df2 = pd.DataFrame(df2)
df2.rename(columns = {'country':'count'}, inplace=True)
df2.reset_index(inplace=True)
df2

df3 = ner_results[['country', 'year']]
df3 = df3.groupby(['country', 'year'])['country'].count()
df3 = pd.DataFrame(df3)
df3.rename(columns = {'country':'count'}, inplace=True)
df3.reset_index(inplace=True)
df3['cat'] = '0'
df3 = df3[['country', 'year', 'cat', 'count']]

df2 = pd.concat([df2, df3])

In [28]:
fig = px.scatter_geo(df2, locations="index", locationmode="country names",
                     size="country", # size of markers, "pop" is one of the columns of gapminder
                     )
fig.show()

In [229]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Choropleth(
    locations = df2['country'],
    z = df2['0'],
    text = df2['country'],
    colorscale = 'Rainbow',
    autocolorscale=False,
    reversescale=False,
    marker_line_color='darkgray',
    marker_line_width=0.5,
    colorbar_tickprefix = '',
    colorbar_title = 'No. Tweets',
    locationmode = 'country names'
))

fig.update_layout(
    title_text='No. Disaster Tweets per Country',
    geo=dict(
        showframe=False,
        showcoastlines=False,
        projection_type='equirectangular'
    ),
    annotations = [dict(
        x=0.55,
        y=0.1,
        xref='paper',
        yref='paper',
        text='Source: NLPower DiMbaT',
        showarrow = False
    )]
)

fig.show()

In [268]:
from urllib.request import urlopen
import json

In [269]:
with urlopen('https://raw.githubusercontent.com/johan/world.geo.json/master/countries.geo.json') as response:
    countries = json.load(response)

In [266]:
countries

{'Afghanistan': 'AFG',
 'Albania': 'ALB',
 'Algeria': 'DZA',
 'American Samoa': 'ASM',
 'Andorra': 'AND',
 'Angola': 'AGO',
 'Anguilla': 'AIA',
 'Antarctica': 'ATA',
 'Antigua and Barbuda': 'ATG',
 'Argentina': 'ARG',
 'Armenia': 'ARM',
 'Aruba': 'ABW',
 'Australia': 'AUS',
 'Austria': 'AUT',
 'Azerbaijan': 'AZE',
 'Bahamas': 'BHS',
 'Bahrain': 'BHR',
 'Bangladesh': 'BGD',
 'Barbados': 'BRB',
 'Belarus': 'BLR',
 'Belgium': 'BEL',
 'Belize': 'BLZ',
 'Benin': 'BEN',
 'Bermuda': 'BMU',
 'Bhutan': 'BTN',
 'Bolivia, Plurinational State of': 'BOL',
 'Bonaire, Sint Eustatius and Saba': 'BES',
 'Bosnia and Herzegovina': 'BIH',
 'Botswana': 'BWA',
 'Bouvet Island': 'BVT',
 'Brazil': 'BRA',
 'British Indian Ocean Territory': 'IOT',
 'Brunei Darussalam': 'BRN',
 'Bulgaria': 'BGR',
 'Burkina Faso': 'BFA',
 'Burundi': 'BDI',
 'Cabo Verde': 'CPV',
 'Cambodia': 'KHM',
 'Cameroon': 'CMR',
 'Canada': 'CAN',
 'Cayman Islands': 'CYM',
 'Central African Republic': 'CAF',
 'Chad': 'TCD',
 'Chile': 'CHL',
 

In [271]:
max_count = df2['0'].max()
fig = px.choropleth_mapbox(df2, geojson=countries,
                      locations='codes', 
                      color='0',
                      color_continuous_scale="Viridis",
                      featureidkey="id",
                      mapbox_style="carto-positron",
                      opacity=0.5,
                      zoom=0.5,
                      animation_frame='year')
fig.update_geos(fitbounds="locations",visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},)
fig.show()

In [156]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import datetime

In [157]:
# mimic OP's datasample

NPERIODS = 200

np.random.seed(123)
df = pd.DataFrame(np.random.randint(-10, 12, size=(NPERIODS, 4)),
                  columns=list('ABCD'))
datelist = pd.date_range(datetime.datetime(2020, 1, 1).strftime('%Y-%m-%d'),
                         periods=NPERIODS).tolist()
df['dates'] = datelist 
df = df.set_index(['dates'])
df.index = pd.to_datetime(df.index)
df.iloc[0] = 0
df = df.cumsum()

In [183]:
df2 = df2.pivot(index=['country', 'year'], columns='cat', values='count')

In [185]:
df2.reset_index(inplace=True)

In [186]:
df2

cat      country  year   1   2    3    4    5    6    7    8    9   10    0
0    Afghanistan  2011 NaN NaN  NaN  1.0  NaN  NaN  NaN  1.0  NaN  NaN  2.0
1    Afghanistan  2013 NaN NaN  NaN  NaN  NaN  NaN  NaN  NaN  1.0  NaN  1.0
2    Afghanistan  2014 NaN NaN  NaN  NaN  NaN  1.0  NaN  NaN  NaN  NaN  1.0
3    Afghanistan  2015 NaN NaN  NaN  NaN  NaN  1.0  NaN  NaN  1.0  NaN  2.0
4    Afghanistan  2017 NaN NaN  1.0  NaN  1.0  NaN  NaN  NaN  1.0  NaN  3.0
..           ...   ...  ..  ..  ...  ...  ...  ...  ...  ...  ...  ...  ...
301      Vietnam  2014 NaN NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  1.0  1.0
302      Vietnam  2016 NaN NaN  NaN  NaN  NaN  NaN  NaN  1.0  NaN  NaN  1.0
303        Yemen  2014 NaN NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  1.0  1.0
304     Zimbabwe  2012 NaN NaN  1.0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  1.0
305     Zimbabwe  2013 NaN NaN  NaN  NaN  NaN  NaN  1.0  NaN  NaN  NaN  1.0

[306 rows x 13 columns]

In [187]:
import plotly.graph_objects as go

In [257]:
max_count = df2['count'].max()
fig = px.choropleth_mapbox(df2, geojson=countries,
                      locations='codes', 
                      color='count',
                      color_continuous_scale="Viridis",
                      featureidkey="id",
                      mapbox_style="carto-positron",
                      opacity=0.5,
                      zoom=0.5,
                      animation_frame='year')
fig.update_geos(fitbounds="locations",visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},)
fig.show()

KeyError: ignored

In [191]:
df2.iloc[:, 3:14].columns

Index([2, 3, 4, 5, 6, 7, 8, 9, 10, '0'], dtype='object', name='cat')

In [201]:
# Data
df = px.data.gapminder().query("year==2007")
df = df.rename(columns=dict(pop="Population",
                            gdpPercap="GDP per Capita",
                            lifeExp="Life Expectancy"))

In [ ]:
import pandas as pd
import numpy as np
import plotly.graph_objs as go
import plotly.express as px

# Data
df = px.data.gapminder().query("year==2007")
df = df.rename(columns=dict(pop="Population",
                            gdpPercap="GDP per Capita",
                            lifeExp="Life Expectancy"))
cols_dd = ["Population", "GDP per Capita", "Life Expectancy"]
# we need to add this to select which trace 
# is going to be visible
visible = np.array(cols_dd)

# define traces and buttons at once
traces = []
buttons = []
for value in cols_dd:
    traces.append(go.Choropleth(
       locations=df['iso_alpha'], # Spatial coordinates
        z=df[value].astype(float), # Data to be color-coded
        colorbar_title=value,
        visible= True if value==cols_dd[0] else False))

    buttons.append(dict(label=value,
                        method="update",
                        args=[{"visible":list(visible==value)},
                              {"title":f"<b>{value}</b>"}]))

updatemenus = [{"active":0,
                "buttons":buttons,
               }]


# Show figure
fig = go.Figure(data=traces,
                layout=dict(updatemenus=updatemenus))
# This is in order to get the first title displayed correctly
first_title = cols_dd[0]
fig.update_layout(title=f"<b>{first_title}</b>",title_x=0.5)
fig.show()

In [214]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Choropleth(
    locations = df2['country'],
    z = df2['0'],
    text = df2['country'],
    colorscale = 'Rainbow',
    autocolorscale=False,
    reversescale=False,
    marker_line_color='darkgray',
    marker_line_width=0.5,
    colorbar_tickprefix = '',
    colorbar_title = 'No. Tweets',
    locationmode = 'country names'
))

fig.update_layout(
    title_text='No. Disaster Tweets per Country',
    geo=dict(
        showframe=False,
        showcoastlines=False,
        projection_type='equirectangular'
    ),
    annotations = [dict(
        x=0.55,
        y=0.1,
        xref='paper',
        yref='paper',
        text='Source: NLPower DiMbaT',
        showarrow = False
    )]
)

fig.show()

In [256]:
import pandas as pd
import plotly.express as px
import json
import plotly



fig = px.choropleth(df2
                    ,locationmode='country names'
                    ,locations = 'country'
                    ,scope = 'world'
                    ,color = "0"
                    ,animation_frame = "year"
                    ,hover_name="country"
                   )

fig["layout"]
fig["layout"].pop("updatemenus")
fig.update_geos(visible=True, showcountries=True, projection_type='natural earth', lonaxis_showgrid=False, lataxis_showgrid=False)

# button with one option for each dataframe
buttons = []
for col in df2.iloc[:, 2:13].columns:
    buttons.append(dict(method='restyle',
                        label=col,
                        args=[{'z':[df2[col]]}, [0]]
                        )
                  )

fig.update_layout(width=1000,
                  coloraxis_colorbar_thickness=23,
                  updatemenus=[dict(y=0.95,
                                    x=0.01,
                                    xanchor='right',
                                    yanchor='top',
                                    active=0,
                                    buttons=buttons)
                              ]) 

In [284]:
fig = px.choropleth_mapbox(df2, geojson=countries,
                      locations='codes', 
                      color='0',
                      color_continuous_scale="Viridis",
                      featureidkey="id",
                      mapbox_style="carto-positron",
                      opacity=0.5,
                      zoom=0.5,
                      animation_frame='year')

fig["layout"]
fig["layout"].pop("updatemenus")
fig.update_geos(fitbounds="locations",visible=False)

buttons = []
for col in df2.iloc[:, 2:13].columns:
    buttons.append(dict(method='update',
                        label=col,
                        args=[{'z-index': 2000000000}, {'color':[df2[col]]}, [0]]
                        )
                  )


fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},width=1000,
                  coloraxis_colorbar_thickness=23,
                  updatemenus=list([dict(y=0.95,
                                    x=0.01,
                                    xanchor='right',
                                    yanchor='top',
                                    active=0,
                                    buttons=buttons)
                              ]))



